In [5]:
import time
import datetime
from keras.models import Sequential
from keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout, BatchNormalization
from keras.preprocessing.image import ImageDataGenerator
from keras.losses import CategoricalCrossentropy
from tensorflow.keras.callbacks import EarlyStopping,LearningRateScheduler
from tensorflow.keras.optimizers import Adam
import tensorflow as tf
from tensorflow.keras import layers, models
from tensorflow.keras.applications import VGG16

from Func.getSubFolders import count_sub_folders
from Func.DrawImages import plot_images


path = 'Data'
output = 'Model/keras_model.h5'
start_time = time.time()

physical_devices = tf.config.list_physical_devices('GPU')
print("Num GPUs Available: ", len(physical_devices))
if len(physical_devices) > 0:
    try:
        # Set memory growth to true
        for device in physical_devices:
            tf.config.experimental.set_memory_growth(device, True)
    except RuntimeError as e:
        print('runtime gpu', e)
else:
    print("No GPU available. Using CPU.")


def lr_schedule(epoch, lr):
    if epoch < 5:
        return lr
    elif epoch < 10:
        return lr * 0.001
    else:
        return lr * 0.01



# Step 1: Load and Preprocess Images
datagen = ImageDataGenerator(
    rescale=1. / 255,
    validation_split=0.2,
    width_shift_range=0.2,
    height_shift_range=0.2,
    shear_range=0.2,
    zoom_range=0.2,
    fill_mode='nearest',
)


# Step 2: Label the Data
train_set = datagen.flow_from_directory(
    path,
    target_size=(224, 224),
    batch_size=16,
    class_mode='categorical',
    subset='training'
)

test_set = datagen.flow_from_directory(
    path,
    target_size=(224, 224),
    batch_size=16,
    class_mode='categorical',
    subset='validation'
)

# draw Images
#images, labels = next(train_set)

#class_indices = test_set.class_indices
#plot_images(images, labels, class_indices)

base_model = VGG16(weights='imagenet', include_top=False, input_shape=(224, 224, 3)) # EXPLAINNNNN
base_model.trainable = False

# Step 4: Build the Model

model = Sequential([
    base_model,
    Flatten(),
    Dense(units=1024, activation='relu'),
    Dropout(0.5),
    Dense(units=512, activation='relu'),
    Dropout(0.5),
    Dense(units=256, activation='relu'),
    Dropout(0.5),
    Dense(units=128, activation='relu'),
    Dropout(0.5),
    Dense(units=count_sub_folders(path), activation='softmax')
])



# Compile the Model
model.compile(optimizer=Adam(learning_rate=0.0001),
              loss=CategoricalCrossentropy(from_logits=False),
              metrics=['accuracy'])

# Step 6: Train the Model
early_stopping = EarlyStopping(monitor='val_loss', patience=5, restore_best_weights=True)
lr_scheduler = LearningRateScheduler(lr_schedule)

model.fit(
    train_set,
    steps_per_epoch=train_set.samples // train_set.batch_size,
    validation_data=test_set,
    validation_steps=test_set.samples // test_set.batch_size,
    epochs=30,
    callbacks=[early_stopping, lr_scheduler]
)

# Step 7: Evaluate the Model
loss, accuracy = model.evaluate(test_set)
print(f'Test loss: {loss}, Test accuracy: {accuracy}')

# Save the trained model
model.save(output)
end_time = time.time()

execute_time = (end_time - start_time) / 60

model.summary()

# Print the result
print("Last build:", datetime.datetime.now().strftime("%d/%m/%y"))
print(f"It took: {execute_time:0.2f} minutes")

Num GPUs Available:  1
Found 4458 images belonging to 6 classes.
Found 1111 images belonging to 6 classes.
Epoch 1/30
278/278 [==============================] - 60s 213ms/step - loss: 1.8360 - accuracy: 0.2733 - val_loss: 1.3567 - val_accuracy: 0.4556 - lr: 1.0000e-04
Epoch 2/30
278/278 [==============================] - 59s 213ms/step - loss: 1.2122 - accuracy: 0.5000 - val_loss: 0.8902 - val_accuracy: 0.8062 - lr: 1.0000e-04
Epoch 3/30
278/278 [==============================] - 59s 214ms/step - loss: 0.7822 - accuracy: 0.6952 - val_loss: 0.6691 - val_accuracy: 0.8469 - lr: 1.0000e-04
Epoch 4/30
278/278 [==============================] - 59s 213ms/step - loss: 0.4722 - accuracy: 0.8253 - val_loss: 0.4470 - val_accuracy: 0.9004 - lr: 1.0000e-04
Epoch 5/30
278/278 [==============================] - 59s 214ms/step - loss: 0.2882 - accuracy: 0.9070 - val_loss: 0.3356 - val_accuracy: 0.9167 - lr: 1.0000e-04
Epoch 6/30
278/278 [==============================] - 59s 214ms/step - loss: 0.2105